## PG Diploma - Machine Learning and Artificial Intelligence

# Lending Club Case Study - Solution

#### By:
1. Prateek Ralhan (Group Facilitator)
2. Harshit Mehta

#### Let us start by stating the objective that we need to accomplish through this assignment.

## Objective:
To identify the risky loan applicants at the time of loan application so that such loans can be reduced thereby cutting down the amount of credit loss. Identification of such applicants using EDA is the aim of this case study.

In other words, to understand the driving factors (or driver variables) behind loan default, i.e. the variables which are strong indicators of default. The company can utilise this knowledge for its portfolio and risk assessment. And thus minimise the risk of losing money while lending to customers.



In [1]:
#importing the necerssary libraries

import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns
from matplotlib import style
import pandas_profiling


In [2]:
df = pd.read_csv('loan.csv',encoding = "ISO-8859-1")

/home/vibertron/environments/venv/lib/python3.5/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (47) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
df.profile_report(style={'full_width':True})

/home/vibertron/environments/venv/lib/python3.5/site-packages/pandas_profiling/__init__.py:53: UserWarning: Sorting is supported from Python 3.6+
  warnings.warn("Sorting is supported from Python 3.6+")


In [4]:
print(df.shape)
df.describe()

(39717, 111)


id     member_id     loan_amnt   funded_amnt  \
count  3.971700e+04  3.971700e+04  39717.000000  39717.000000   
mean   6.831319e+05  8.504636e+05  11219.443815  10947.713196   
std    2.106941e+05  2.656783e+05   7456.670694   7187.238670   
min    5.473400e+04  7.069900e+04    500.000000    500.000000   
25%    5.162210e+05  6.667800e+05   5500.000000   5400.000000   
50%    6.656650e+05  8.508120e+05  10000.000000   9600.000000   
75%    8.377550e+05  1.047339e+06  15000.000000  15000.000000   
max    1.077501e+06  1.314167e+06  35000.000000  35000.000000   

       funded_amnt_inv   installment    annual_inc           dti  \
count     39717.000000  39717.000000  3.971700e+04  39717.000000   
mean      10397.448868    324.561922  6.896893e+04     13.315130   
std        7128.450439    208.874874  6.379377e+04      6.678594   
min           0.000000     15.690000  4.000000e+03      0.000000   
25%        5000.000000    167.020000  4.040400e+04      8.170000   
50%        8975.000000    280.220000  5.900000e+04     13.400000   
75%       14400.000000    430.780000  8.230000e+04     18.600000   
max       35000.000000   1305.190000  6.000000e+06     29.990000   

        delinq_2yrs  inq_last_6mths             ...              \
count  39717.000000    39717.000000             ...               
mean       0.146512        0.869200             ...               
std        0.491812        1.070219             ...               
min        0.000000        0.000000             ...               
25%        0.000000        0.000000             ...               
50%        0.000000        1.000000             ...               
75%        0.000000        1.000000             ...               
max       11.000000        8.000000             ...               

       num_tl_90g_dpd_24m  num_tl_op_past_12m  pct_tl_nvr_dlq  \
count                 0.0                 0.0             0.0   
mean                  NaN                 NaN             NaN   
std                   NaN                 NaN             NaN   
min                   NaN                 NaN             NaN   
25%                   NaN                 NaN             NaN   
50%                   NaN                 NaN             NaN   
75%                   NaN                 NaN             NaN   
max                   NaN                 NaN             NaN   

       percent_bc_gt_75  pub_rec_bankruptcies  tax_liens  tot_hi_cred_lim  \
count               0.0          39020.000000    39678.0              0.0   
mean                NaN              0.043260        0.0              NaN   
std                 NaN              0.204324        0.0              NaN   
min                 NaN              0.000000        0.0              NaN   
25%                 NaN              0.000000        0.0              NaN   
50%                 NaN              0.000000        0.0              NaN   
75%                 NaN              0.000000        0.0              NaN   
max                 NaN              2.000000        0.0              NaN   

       total_bal_ex_mort  total_bc_limit  total_il_high_credit_limit  
count                0.0             0.0                         0.0  
mean                 NaN             NaN                         NaN  
std                  NaN             NaN                         NaN  
min                  NaN             NaN                         NaN  
25%                  NaN             NaN                         NaN  
50%                  NaN             NaN                         NaN  
75%                  NaN             NaN                         NaN  
max                  NaN             NaN                         NaN  

[8 rows x 87 columns]

# 1. Data Cleaning :)

In [5]:
#finding missing values in % per column
missing = round(100*(df.isnull().sum()/len(df.id)), 2)
missing.loc[missing > 0]

emp_title                           6.19
emp_length                          2.71
desc                               32.58
title                               0.03
mths_since_last_delinq             64.66
mths_since_last_record             92.99
revol_util                          0.13
last_pymnt_d                        0.18
next_pymnt_d                       97.13
last_credit_pull_d                  0.01
collections_12_mths_ex_med          0.14
mths_since_last_major_derog       100.00
annual_inc_joint                  100.00
dti_joint                         100.00
verification_status_joint         100.00
tot_coll_amt                      100.00
tot_cur_bal                       100.00
open_acc_6m                       100.00
open_il_6m                        100.00
open_il_12m                       100.00
open_il_24m                       100.00
mths_since_rcnt_il                100.00
total_bal_il                      100.00
il_util                           100.00
open_rv_12m     

We observe that many columns in our dataset has 100% missing values. 
Lets remove all the columns with more than 50% missing values.

In [6]:
#finding total no of columns with greater than/equal to 50% missing values
missing_columns = list(missing[missing >= 50].index)

len(missing_columns)

57

We observe that **57** columns have more than 50% missing values. Let us remove thes columns as they don't seem to be significant in our analysis.

In [7]:
print("Actual Shape :",df.shape)

df = df.drop(missing_columns,axis=1)
print("Shape after removing missing values with >=50% :",df.shape)




Actual Shape : (39717, 111)
Shape after removing missing values with >=50% : (39717, 54)


We have **54** columns remaining now. Let's clean it up further :)

In [8]:
#Further looking into remaining miss values

missing_remaining = round(100*(df.isnull().sum()/len(df.id)), 2)
missing_remaining[missing_remaining != 0]

emp_title                      6.19
emp_length                     2.71
desc                          32.58
title                          0.03
revol_util                     0.13
last_pymnt_d                   0.18
last_credit_pull_d             0.01
collections_12_mths_ex_med     0.14
chargeoff_within_12_mths       0.14
pub_rec_bankruptcies           1.75
tax_liens                      0.10
dtype: float64

Let us remove the **desc** column, which comprises of the loan description provided by the borrower, as similar short and consise information is present in the **title** and **purpose** columns of the dataset.

In [9]:
#dropping the desc column
df = df.drop('desc',axis=1)

In [10]:
#Finding no. of unique values for the remaining columns:

print("no. of unique values for \"emp_title\" :",len(df.emp_title.unique()))
print("no. of unique values for \"emp_length\" :",len(df.emp_length.unique()))
print("no. of unique values for \"title\" :",len(df.title.unique()))
print("no. of unique values for \"revol_util\" :",len(df.revol_util.unique()))
print("no. of unique values for \"last_pymnt_d\" :",len(df.last_pymnt_d.unique()))
print("no. of unique values for \"last_credit_pull_d\" :",len(df.last_credit_pull_d.unique()))
print("no. of unique values for \"collections_12_mths_ex_med\" :",len(df.collections_12_mths_ex_med.unique()))
print("no. of unique values for \"chargeoff_within_12_mths\" :",len(df.chargeoff_within_12_mths.unique()))
print("no. of unique values for \"pub_rec_bankruptcies\" :",len(df.pub_rec_bankruptcies.unique()))
print("no. of unique values for \"tax_liens\" :",len(df.tax_liens.unique()))

no. of unique values for "emp_title" : 28821
no. of unique values for "emp_length" : 12
no. of unique values for "title" : 19616
no. of unique values for "revol_util" : 1090
no. of unique values for "last_pymnt_d" : 102
no. of unique values for "last_credit_pull_d" : 107
no. of unique values for "collections_12_mths_ex_med" : 2
no. of unique values for "chargeoff_within_12_mths" : 2
no. of unique values for "pub_rec_bankruptcies" : 4
no. of unique values for "tax_liens" : 2


Columns **emp_length**, **collections_12_mths_ex_med**, **chargeoff_within_12_mths**, **pub_rec_bankruptcies** and **tax_liens** are categorical in nature.

Let us have a look at them :)


In [11]:
print("Different values of \"emp_length\": ",df.emp_length.unique(),"\n")
print("Different values of \"collections_12_mths_ex_med\": ",df.collections_12_mths_ex_med.unique(),"\n")
print("Different values of \"chargeoff_within_12_mths\": ",df.chargeoff_within_12_mths.unique(),"\n")
print("Different values of \"pub_rec_bankruptcies\": ",df.pub_rec_bankruptcies.unique(),"\n")
print("Different values of \"tax_liens\": ",df.tax_liens.unique(),"\n")

Different values of "emp_length":  ['10+ years' '< 1 year' '1 year' '3 years' '8 years' '9 years' '4 years'
 '5 years' '6 years' '2 years' '7 years' nan] 

Different values of "collections_12_mths_ex_med":  [ 0. nan] 

Different values of "chargeoff_within_12_mths":  [ 0. nan] 

Different values of "pub_rec_bankruptcies":  [ 0.  1.  2. nan] 

Different values of "tax_liens":  [ 0. nan] 



The columns **collections_12_mths_ex_med**, **chargeoff_within_12_mths** and **tax_liens** only have values **0** or **nan**. With this range in their values, they won't have any necessary impact on our analysis.
Let us drop these columns as a part of our analysis.

In [12]:
drop_columns = ['collections_12_mths_ex_med', 'chargeoff_within_12_mths', 'tax_liens']
df = df.drop(drop_columns,axis=1)

In [13]:
df.shape

(39717, 50)

Next, let us analyse the columng **pub_rec_bankruptcies** which talks about the past number of public record bankruptcies.

In [14]:
df.pub_rec_bankruptcies.value_counts()

0.0    37339
1.0     1674
2.0        7
Name: pub_rec_bankruptcies, dtype: int64

**pub_rec_bankruptcies** has 3 kind of values - **0,1 and 2** with ~37000, ~1700 and 7 records respectively.

Though we can take the mode representation of the data which is **0** bankrupcies for imputing the missing values. But, we decide to drop the missing rows as a precautionary measure to ensure that we don't add any unnecessary bias in our dataset.



In [15]:
df=df[~df.pub_rec_bankruptcies.isnull()]

In [16]:
missing = round(100*(df.isnull().sum()/len(df.id)), 2) 
missing[missing != 0]

emp_title       6.19
emp_length      2.75
title           0.03
revol_util      0.13
last_pymnt_d    0.18
dtype: float64

The columns **emp_title** and **emp_length** have 6.19% and 2.71% missing values. These columns have information about the customer/borrower like their job title and their employment length in years. 

Let's drop the rows with missing values for these columns :)

In [17]:
df=df[~df.emp_title.isnull()]
df=df[~df.emp_length.isnull()]

In [18]:
print(df.shape)

(36548, 50)


Now, we are left with **title**, **revol_util** and **last_pymnt_d** with minimal amount of missing values - 0.02%, 0.13% and 0.18% respectively.
**title** tells us about the title of the loan specified by the borrower in the application.
**revol_util** gives the revolving line utelization and
**last_pymnt_d** gives the month in which last payment was received.

Let's again remove the rows with missing values for these columns.


In [19]:
df=df[~df.title.isnull()]
df=df[~df.revol_util.isnull()]
df=df[~df.last_pymnt_d.isnull()]

In [20]:
df.shape

(36433, 50)

In [21]:
missing =round(100*(df.isnull().sum()/len(df.id)), 2) 
missing[missing != 0]


Series([], dtype: float64)

### Now, we have our dataset cleaned up and ready for indepth analysis :)
After suitable cleaning, it has 36433 loan records and 50 attributes with no missing values. 

As a sanity check, let us save it into another file ***clean.csv*** and use it for further analysis

In [22]:
df.to_csv('clean.csv', encoding='ISO-8859-1', index=False)

In [23]:
cleaned_data = pd.read_csv('clean.csv',encoding='utf-8')

In [24]:
cleaned_data.nunique().sort_values()

acc_now_delinq                 1
application_type               1
policy_code                    1
initial_list_status            1
delinq_amnt                    1
pymnt_plan                     1
term                           2
pub_rec_bankruptcies           3
loan_status                    3
verification_status            3
home_ownership                 4
pub_rec                        5
grade                          7
inq_last_6mths                 9
delinq_2yrs                   11
emp_length                    11
purpose                       14
sub_grade                     35
open_acc                      38
addr_state                    49
issue_d                       52
total_acc                     79
last_credit_pull_d            96
last_pymnt_d                  97
int_rate                     334
earliest_cr_line             510
zip_code                     806
loan_amnt                    863
funded_amnt                 1024
out_prncp                   1064
out_prncp_

Let's make use of ***Data_dictionary.xlsx*** to get a better understanding of the remaining 50 columns.

Some columns possess a single unique value or all unique values. These may not be significant enough to contribute to the analysis i.e. columns which are far from being the **crucial columns towards loan default**. Some columns also seem to be unessential.

They are given as follows:

   1. **id** :
   It's a random number given to the loan. - **NOT NEEDED FOR ANALYSIS**
   2. **member_id** :
   It's a random number given to the member -  **NOT NEEDED FOR ANALYSIS**
   3. **pymnt_plan** :
    It's value for all the rows is 'n',  **CAN BE DROPPED**
   4. **url** :
 It's a URL for LC page for corresponding to each memberid,**not needed for loan default - CAN BE DROPPED**.
   5. **zip_code** :
    first 3 digits of the 5 digit zip code are visible, also is redundant with addr_state - **NOT NEEDED FOR ANALYSIS**
   6. **initial_list_status** :
    It's value for all the rows is 'f' out of the possible values -  **CAN BE DROPPED**
   7. **policy_code** :
    It's value for all the rows is '1', which means all are publicly available.Thus, it doesn't contribute for analysis -  **CAN BE DROPPED**
   8. **application_type** :
    It's value for all the rows is 'INDIVIDUAL' -  **CAN BE DROPPED**
   9. **acc_now_delinq** :
    It's value for all the rows is '0' -  **CAN BE DROPPED**
   10. **delinq_amnt** :
    It's value for all the rows is '0' - **CAN BE DROPPED**
   11. **funded_amnt** :
    It's value is almost similar to ***loan_amnt*** - **CAN BE DROPPED**
   12. **funded_amnt_inv** :
    It's is highly correlated with ***funded_amnt***. Also this wont be available at the time of decision making of funding a loan - **CAN BE DROPPED**

Dropping the above columns from the cleaned_data dataframe.


In [25]:
dropped_cols = ['id','member_id','funded_amnt','funded_amnt_inv','pymnt_plan','url','zip_code','initial_list_status','policy_code','application_type','acc_now_delinq','delinq_amnt',]
cleaned_data= cleaned_data.drop(dropped_cols,axis=1)


In [26]:
cleaned_data.shape

(36433, 38)

We have now reduced down our domain for analysis  to 38 columns.

Next thing that we can do is to standardize the dataset precision values. We can round off the values for  certain columns up until two decimal places.
These columns are:

   - total_pymnt
   - total_rec_late_fee
   - collection_recovery_fee



In [27]:
cleaned_data.total_pymnt.value_counts().tail()

10417.384800    1
14040.768530    1
8954.809409     1
4561.076763     1
4608.000000     1
Name: total_pymnt, dtype: int64

In [28]:
cleaned_data.total_rec_late_fee.value_counts().tail()

14.971231    1
52.840000    1
14.997547    1
33.483779    1
17.165009    1
Name: total_rec_late_fee, dtype: int64

In [29]:
cleaned_data.collection_recovery_fee.value_counts().tail()

9.6738      1
33.2896     1
6.9239      1
340.0000    1
258.9138    1
Name: collection_recovery_fee, dtype: int64

In [30]:
cleaned_data.total_pymnt= round(cleaned_data.total_pymnt,2)
cleaned_data.total_rec_late_fee= round(cleaned_data.total_rec_late_fee,2)
cleaned_data.collection_recovery_fee= round(cleaned_data.collection_recovery_fee,2)

We observed that there are few attributes comprising of date/month information but are of the **type object** in the dataset. Let us modify the dtype of all such attributes to **datetime**. This may help us later for further analysis by using their values.

These columns are:

   - issue_d
   - earliest_cr_line
   - last_pymnt_d
   - last_credit_pull_d



In [31]:
date_time_cols=['issue_d','earliest_cr_line','last_pymnt_d','last_credit_pull_d']
cleaned_data[date_time_cols].info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 36433 entries, 0 to 36432
Data columns (total 4 columns):
issue_d               36433 non-null object
earliest_cr_line      36433 non-null object
last_pymnt_d          36433 non-null object
last_credit_pull_d    36433 non-null object
dtypes: object(4)
memory usage: 1.1+ MB


Converting the dtype of these columns to ***datetime*** :)

In [32]:
cleaned_data.issue_d = pd.to_datetime(cleaned_data.issue_d, format='%b-%y')
cleaned_data.earliest_cr_line = pd.to_datetime(cleaned_data.earliest_cr_line, format='%b-%y')
cleaned_data.last_pymnt_d = pd.to_datetime(cleaned_data.last_pymnt_d, format='%b-%y')
cleaned_data.last_credit_pull_d = pd.to_datetime(cleaned_data.last_credit_pull_d, format='%b-%y')

In [33]:
cleaned_data[date_time_cols].info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 36433 entries, 0 to 36432
Data columns (total 4 columns):
issue_d               36433 non-null datetime64[ns]
earliest_cr_line      36433 non-null datetime64[ns]
last_pymnt_d          36433 non-null datetime64[ns]
last_credit_pull_d    36433 non-null datetime64[ns]
dtypes: datetime64[ns](4)
memory usage: 1.1 MB


In [34]:
# dropping Duplicated rows if any,
cleaned_data=cleaned_data.drop_duplicates()

Some columns are expressing values with **%** sign along with them. They are:
 - int_rate
 - revol_util.

Also, these columns have dtype as **'object'**. Let us drop the **%** sign from these columns and also typecast them to **float**.

In [35]:
cleaned_data.int_rate.describe()

count      36433
unique       334
top       10.99%
freq         901
Name: int_rate, dtype: object

In [36]:
cleaned_data.revol_util.describe()

count     36433
unique     1082
top          0%
freq        852
Name: revol_util, dtype: object

In [37]:
cleaned_data['int_rate'] = cleaned_data['int_rate'].str.strip('%').astype('float')
cleaned_data['revol_util'] = cleaned_data['revol_util'].str.strip('%').astype('float')

In [38]:
cleaned_data[['int_rate','revol_util']].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 36433 entries, 0 to 36432
Data columns (total 2 columns):
int_rate      36433 non-null float64
revol_util    36433 non-null float64
dtypes: float64(2)
memory usage: 853.9 KB


Let us now give a glance to the **emp_length** column.

In [39]:
cleaned_data.emp_length.value_counts()

10+ years    8407
2 years      4178
< 1 year     4052
3 years      3914
4 years      3297
5 years      3129
1 year       3026
6 years      2121
7 years      1697
8 years      1405
9 years      1207
Name: emp_length, dtype: int64

According to **data_dictionary.xlsx**, 
 - **emp_length** :  
 Employment length in years. Possible values are between 0 and 10 where 0 means less than one year and 10 means ten or more years.
 
Let's convert the column to have values between 0 and 10. We can do this by creating a dictionary and replacing them with the corresponding values.

In [40]:
emp_length_dict = {
    '< 1 year' : 0,
    '1 year' : 1,
    '2 years' : 2,
    '3 years' : 3,
    '4 years' : 4,
    '5 years' : 5,
    '6 years' : 6,
    '7 years' : 7,
    '8 years' : 8,
    '9 years' : 9,
    '10+ years' : 10
}


cleaned_data = cleaned_data.replace({"emp_length": emp_length_dict })
cleaned_data.emp_length.value_counts()

10    8407
2     4178
0     4052
3     3914
4     3297
5     3129
1     3026
6     2121
7     1697
8     1405
9     1207
Name: emp_length, dtype: int64

According to **data_dictionary.xlsx**,
 - **term** :
 The number of payments on the loan. 
Values are in months and can be either 36 or 60. Let us remove the string ***months*** from the values present in the column.

In [41]:
cleaned_data.term.value_counts()

 36 months    26377
 60 months    10056
Name: term, dtype: int64

In [42]:
cleaned_data['term'] = cleaned_data.term.apply(lambda x: x.split()[0])
cleaned_data.term.value_counts()

36    26377
60    10056
Name: term, dtype: int64

According to **data_dictionary.xlsx**,

- **earliest_cr_line**: 
The month the borrower's earliest reported credit line was opened. 
We shall split the date column into earliest_cr_line_month and earliest_cr_line_year
We shall also split the available date into month and year attributes.


In [43]:
cleaned_data['earliest_cr_line_month'] = cleaned_data['earliest_cr_line'].dt.month
cleaned_data['earliest_cr_line_year'] = cleaned_data['earliest_cr_line'].dt.year

In [44]:
len(cleaned_data[cleaned_data['earliest_cr_line_year'] > 2011 ])

50

Thus, we observe that there are 50 records with the earliest credit line date greater than 2011 (which is the max range of the data we have).
Let us analyse further.

In [45]:
cleaned_data[cleaned_data['earliest_cr_line_year'] > 2011 ]['earliest_cr_line_year'].unique()

array([2068, 2067, 2065, 2063, 2066, 2062, 2056, 2046, 2050, 2064, 2054])

In [46]:
cleaned_data.loc[cleaned_data['earliest_cr_line_year'] > 2011 , 'earliest_cr_line_year'] = cleaned_data['earliest_cr_line_year'] - 100

In [47]:
cleaned_data.groupby('earliest_cr_line_year').loan_amnt.count()

earliest_cr_line_year
1946       1
1950       1
1954       1
1956       1
1962       3
1963       4
1964       2
1965       6
1966       7
1967      12
1968      12
1969      22
1970      35
1971      34
1972      33
1973      41
1974      51
1975      57
1976      73
1977      90
1978     130
1979     141
1980     150
1981     154
1982     196
1983     296
1984     360
1985     406
1986     447
1987     565
1988     671
1989     781
1990     944
1991     884
1992     970
1993    1398
1994    1860
1995    1974
1996    2074
1997    2271
1998    2645
1999    2763
2000    3034
2001    2363
2002    1794
2003    1740
2004    1639
2005    1406
2006    1079
2007     668
2008     144
Name: loan_amnt, dtype: int64

 According to **data_dictionary.xlsx**,
 
 - **issue_d**: 
 The month which the loan was funded.
 
 Let us split the available date into month and year columns respectively.


In [48]:
cleaned_data['issue_d_month'] = cleaned_data['issue_d'].dt.month
cleaned_data['issue_d_year'] = cleaned_data['issue_d'].dt.year

### Saving the refined data to file - ****MASTER.csv****. We shall work on this fine-tuned data for further analysis.

In [49]:
cleaned_data.to_csv('MASTER.csv', encoding='ISO-8859-1', index=False)

# 2. Data Analysis :)

In [50]:
master=pd.read_csv('MASTER.csv', encoding='ISO-8859-1')

In [51]:
print(master.shape)
master.loan_status.value_counts()

(36433, 42)


Fully Paid     30424
Charged Off     4943
Current         1066
Name: loan_status, dtype: int64